In [1]:
import pandas as pd
import numpy as np
import warnings 
import nltk
import matplotlib.pyplot as plt
from nltk.tokenize import RegexpTokenizer
from nltk.corpus import stopwords
from nltk.stem import WordNetLemmatizer
from nltk.tokenize import word_tokenize
import re
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.decomposition import LatentDirichletAllocation
from sklearn.model_selection import train_test_split
from gensim.models import LdaModel
from gensim.models.coherencemodel import CoherenceModel
from gensim import corpora
from gensim.corpora import Dictionary
from datetime import datetime

In [2]:
import pyLDAvis
import pyLDAvis.gensim_models

In [3]:
warnings.filterwarnings('ignore')

In [4]:
#data =  pd.read_csv('data_processed.csv',  engine = 'python',  on_bad_lines = 'skip', index_col=[0])

In [5]:
data =  pd.read_csv('data_processed.csv',  engine = 'python',  on_bad_lines = 'skip')

In [6]:
data.columns

Index(['Id', 'Title', 'Title_tokens', 'Body', 'Body_tokens', 'Tags',
       'Tag_token', 'Score', 'AnswerCount'],
      dtype='object')

In [7]:
data.shape

(50000, 9)

In [8]:
X = data[['Title_tokens', 'Body_tokens','Tag_token','Score', 'AnswerCount']]
y = data[['Tag_token']]

# re tokenisations des variables tockens suite à la lecture csv qui lit champe en string,  mise à jour aussi dans dataframe data. 
X['Title_tokens'] = X['Title_tokens'].apply(lambda x: re.sub('[^a-zA-Z_]', ' ', str(x)))
X['Title_tokens'] = X['Title_tokens'].apply(nltk.word_tokenize)
X['Body_tokens'] = X['Body_tokens'].apply(lambda x: re.sub('[^a-zA-Z_]', ' ', str(x)))
X['Body_tokens'] = X['Body_tokens'].apply(nltk.word_tokenize)
X['Tag_token'] = X['Tag_token'].apply(lambda x: re.sub('[^a-zA-Z_]', ' ', str(x)))
X['Tag_token'] = X['Tag_token'].apply(nltk.word_tokenize)

# Split the Title_tokens into train and test sets
X_train, X_test = train_test_split(X, test_size=0.2, random_state=42)

X_train_title = X_train['Title_tokens']
X_test_title = X_test['Title_tokens']
X_train_body = X_train['Body_tokens']
X_test_body = X_test['Body_tokens']
X_train_tag = X_train['Tag_token']
X_test_tag = X_test['Tag_token']

In [9]:
X_train_title.head()

39087                                  [stored, procedure]
30893                         [run, fly, tomcat, netbeans]
45278    [show, gray, color, view, io, navigation, bar,...
16398    [form, authentication, ticket, decryption, pos...
13653                                    [validation, yii]
Name: Title_tokens, dtype: object

In [10]:
X_test_tag.head()

33553         [javascript, jquery, html, css, tablesorter]
9427               [php, mysql, file, codeigniter, upload]
199      [python, python, x, csv, dictionary, multidime...
12447               [php, net, frameworks, ldap, openldap]
39489    [vue, js, vuejs, datepicker, vue, component, v...
Name: Tag_token, dtype: object

# 3. Modèles non supervisés

Nous utilisons LDA comme le modèle non supervisé.  LDA entrainé est utilisée pour découvrir des sujets cachés dans les nouveaux documents. 
Les mots les plus probables dans ces sujets découverts sont généralement considérés comme les mots-clés les plus pertinents pour le document.

In [11]:
performance_list = []
pyLDAvis.enable_notebook()

# 3.1 Entrainement et nombre de topics

In [12]:
def lda_train(num_topics, X_train):
    # Create a dictionary and bag-of-words representation of the training data
    dictionary = Dictionary(X_train)
    bow_corpus = [dictionary.doc2bow(doc) for doc in X_train]
    
    # Train the LDA model
    lda_model = LdaModel(corpus=bow_corpus, num_topics=num_topics, id2word=dictionary)

    topics = lda_model.get_document_topics(bow_corpus)
    
    #  Visulisation des topics 
#    vis = pyLDAvis.gensim_models.prepare(topic_model=lda_model, corpus=bow_corpus, dictionary=dictionary, mds='mmds', R=30)
    vis = pyLDAvis.gensim_models.prepare(topic_model=lda_model, corpus=bow_corpus, dictionary=dictionary, mds='pcoa', sort_topics=True)
    
    # Calculer la perplexité
    perplexity = lda_model.log_perplexity(bow_corpus)

    # Calculer la cohérence des topics
    coherence_model = CoherenceModel(model=lda_model, texts=X_train, corpus=bow_corpus, coherence='c_v')
    coherence_score = coherence_model.get_coherence()
    
    return perplexity, coherence_score, lda_model, vis

### 3.1.1 Modèle 1: LDA entrainement avec titre

In [13]:
num_topics = 10
perplexity_titre, coherence_score_titre, lda_titre, vis_titre = lda_train(num_topics, X_train_title)
current_datetime = datetime.now()
formatted_datetime = current_datetime.strftime("%Y-%m-%d %H:%M:%S")
y_resultat = [formatted_datetime, 'lda train avec titre', num_topics, perplexity_titre, coherence_score_titre]
performance_list.append(y_resultat)
vis_titre

PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
9     -0.014441  0.058366       1        1  12.218895
7      0.159822  0.011127       2        1  10.578848
0     -0.212859 -0.032901       3        1  10.468061
6      0.127207  0.175898       4        1  10.464849
8     -0.025296 -0.213217       5        1  10.195269
2     -0.094463 -0.144058       6        1  10.027184
3     -0.060348 -0.060001       7        1   9.809880
1      0.036745 -0.011061       8        1   9.216319
4      0.246001 -0.042814       9        1   8.624557
5     -0.162368  0.258660      10        1   8.396137, topic_info=       Term         Freq        Total Category  logprob  loglift
117   image  1188.000000  1188.000000  Default  30.0000  30.0000
186  object  1193.000000  1193.000000  Default  29.0000  29.0000
144     sql   958.000000   958.000000  Default  28.0000  28.0000
168    user   729.000000   729.000000  Default  27.0000  27.0000
212    list   815.000000   815.000000  Default  26.0000  26.0000
..      ...          ...          ...      ...      ...      ...
547   state   122.336997   159.300719  Topic10  -5.0125   2.2134
584  action   142.388743   243.757144  Topic10  -4.8607   1.9398
117   image   166.563378  1188.911976  Topic10  -4.7039   0.5120
4       run   139.484414   511.234327  Topic10  -4.8813   1.1785
709    test   126.232792   465.816251  Topic10  -4.9812   1.1717

[634 rows x 6 columns], token_table=      Topic      Freq    Term
term                         
584       1  0.008205  action
584       2  0.008205  action
584       4  0.217430  action
584       8  0.184610  action
584      10  0.582547  action
...     ...       ...     ...
341       6  0.209722     xml
341       7  0.294380     xml
341       8  0.092355     xml
341      10  0.109671     xml
21        1  0.974739     yii

[1605 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[10, 8, 1, 7, 9, 3, 4, 2, 5, 6])

In [14]:
num_topics = 20
perplexity_titre, coherence_score_titre, lda_titre, vis_titre = lda_train(num_topics, X_train_title)
current_datetime = datetime.now()
formatted_datetime = current_datetime.strftime("%Y-%m-%d %H:%M:%S")
y_resultat = [formatted_datetime, 'lda train avec titre', num_topics, perplexity_titre, coherence_score_titre]
performance_list.append(y_resultat)
vis_titre

PreparedData(topic_coordinates=              x         y  topics  cluster      Freq
topic                                               
11    -0.172932  0.027165       1        1  6.549870
12    -0.037643 -0.187158       2        1  5.783554
17    -0.075033 -0.067442       3        1  5.588373
0      0.232417  0.024210       4        1  5.433871
2     -0.071877 -0.161995       5        1  5.363760
7      0.033915 -0.147909       6        1  5.363577
4     -0.139814  0.120964       7        1  5.215145
15     0.007911 -0.071930       8        1  5.157450
14     0.062650  0.180857       9        1  5.153410
8      0.075385 -0.012944      10        1  4.984821
1     -0.077145  0.044270      11        1  4.898680
13    -0.141938  0.016749      12        1  4.893313
10     0.248432 -0.023394      13        1  4.882658
3     -0.066185  0.035992      14        1  4.640982
9      0.088897  0.151034      15        1  4.557921
16    -0.020503  0.239445      16        1  4.486752
18     0.170435 -0.049919      17        1  4.434746
5     -0.083876  0.055518      18        1  4.391370
6      0.021214 -0.044028      19        1  4.266840
19    -0.054310 -0.129485      20        1  3.952909, topic_info=          Term         Freq        Total Category  logprob  loglift
237     server  1322.000000  1322.000000  Default  30.0000  30.0000
186     object  1238.000000  1238.000000  Default  29.0000  29.0000
92     android  1281.000000  1281.000000  Default  28.0000  28.0000
144        sql  1021.000000  1021.000000  Default  27.0000  27.0000
209        app  1165.000000  1165.000000  Default  26.0000  26.0000
..         ...          ...          ...      ...      ...      ...
61      inside    97.557642   511.713216  Topic20  -4.4855   1.5734
663   password    77.533727   141.715185  Topic20  -4.7153   2.6276
755    angular    87.439704   456.550729  Topic20  -4.5950   1.5780
329   function    91.337139  1207.784453  Topic20  -4.5514   0.6487
470  different    86.877331   662.259456  Topic20  -4.6015   1.1996

[980 rows x 6 columns], token_table=      Topic      Freq     Term
term                          
783       7  0.984827     able
839       6  0.003976   access
839       7  0.833048   access
839       8  0.131220   access
839      11  0.011929   access
...     ...       ...      ...
341      20  0.001782      xml
2041     11  0.979958    xpath
21        3  0.979057      yii
1284     17  0.979112  youtube
1686     15  0.978395     zoom

[2291 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[12, 13, 18, 1, 3, 8, 5, 16, 15, 9, 2, 14, 11, 4, 10, 17, 19, 6, 7, 20])

In [15]:
num_topics = 30
perplexity_titre, coherence_score_titre, lda_titre, vis_titre = lda_train(num_topics, X_train_title)
current_datetime = datetime.now()
formatted_datetime = current_datetime.strftime("%Y-%m-%d %H:%M:%S")
y_resultat = [formatted_datetime, 'lda train avec titre', num_topics, perplexity_titre, coherence_score_titre]
performance_list.append(y_resultat)
vis_titre

PreparedData(topic_coordinates=              x         y  topics  cluster      Freq
topic                                               
10     0.149641  0.054810       1        1  4.045414
13    -0.156022 -0.041556       2        1  4.007577
14    -0.146114  0.116995       3        1  3.879827
12    -0.023508 -0.116924       4        1  3.866910
25     0.061597 -0.043678       5        1  3.601161
29    -0.133716  0.110208       6        1  3.583647
7      0.024050 -0.175908       7        1  3.562650
5     -0.020300 -0.165379       8        1  3.473778
24     0.074080  0.105500       9        1  3.467514
3      0.026697 -0.121085      10        1  3.439954
22    -0.170194 -0.079253      11        1  3.412856
27    -0.012962 -0.046663      12        1  3.351159
9     -0.017354 -0.061797      13        1  3.342931
21     0.124241  0.110682      14        1  3.339819
23    -0.203160  0.172849      15        1  3.337563
17    -0.087973 -0.080895      16        1  3.337407
8      0.067250 -0.137417      17        1  3.307268
0      0.085899  0.140531      18        1  3.292688
16     0.094131  0.063808      19        1  3.280428
18     0.053041  0.006298      20        1  3.270455
28     0.051334 -0.019595      21        1  3.226871
19    -0.117002  0.024907      22        1  3.198831
2     -0.033827  0.040553      23        1  3.165021
4      0.135119 -0.022945      24        1  3.144873
20     0.036450  0.026691      25        1  3.144611
11     0.026958  0.036714      26        1  3.013028
26    -0.076164 -0.026856      27        1  2.971400
15     0.108198 -0.010814      28        1  2.804182
6      0.008098  0.018653      29        1  2.583749
1      0.071513  0.121565      30        1  2.546427, topic_info=          Term         Freq        Total Category  logprob  loglift
117      image  1295.000000  1295.000000  Default  30.0000  30.0000
237     server  1327.000000  1327.000000  Default  29.0000  29.0000
186     object  1286.000000  1286.000000  Default  28.0000  28.0000
78     working  1021.000000  1021.000000  Default  27.0000  27.0000
188      array  1094.000000  1094.000000  Default  26.0000  26.0000
...        ...          ...          ...      ...      ...      ...
1468   address   160.332847   173.490424  Topic30  -3.5490   3.5916
845   datetime    93.788661   100.846392  Topic30  -4.0852   3.5979
1409      main    90.502677   108.299291  Topic30  -4.1208   3.4910
306   redirect   124.740425   216.496182  Topic30  -3.8000   3.1191
399     window    63.490353  1106.265028  Topic30  -4.4753   0.8126

[1215 rows x 6 columns], token_table=      Topic      Freq     Term
term                          
783      14  0.013009     able
783      17  0.962680     able
839       6  0.001981   access
839      12  0.001981   access
839      13  0.978692   access
...     ...       ...      ...
2041     25  0.975348    xpath
21       13  0.980497      yii
1284     20  0.976549  youtube
2437     30  0.974394     zend
1686     25  0.981015     zoom

[2351 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[11, 14, 15, 13, 26, 30, 8, 6, 25, 4, 23, 28, 10, 22, 24, 18, 9, 1, 17, 19, 29, 20, 3, 5, 21, 12, 27, 16, 7, 2])

In [16]:
num_topics = 50
perplexity_titre, coherence_score_titre, lda_titre, vis_titre = lda_train(num_topics, X_train_title)
current_datetime = datetime.now()
formatted_datetime = current_datetime.strftime("%Y-%m-%d %H:%M:%S")
y_resultat = [formatted_datetime, 'lda train avec titre', num_topics, perplexity_titre, coherence_score_titre]
performance_list.append(y_resultat)
vis_titre

PreparedData(topic_coordinates=              x         y  topics  cluster      Freq
topic                                               
7     -0.093343  0.100828       1        1  2.752786
40     0.021506  0.123913       2        1  2.678647
6      0.066047 -0.108444       3        1  2.500502
13    -0.211383  0.008331       4        1  2.485424
4     -0.018293 -0.061842       5        1  2.474217
33    -0.033906 -0.139855       6        1  2.415476
23     0.122803 -0.044582       7        1  2.388698
15    -0.154588  0.056784       8        1  2.315947
44     0.097160  0.098682       9        1  2.280417
39    -0.051944 -0.070465      10        1  2.249953
0      0.047620 -0.027352      11        1  2.243283
10    -0.115415  0.023856      12        1  2.241318
3     -0.054523  0.001332      13        1  2.226139
25     0.122307 -0.114681      14        1  2.225856
34     0.008740 -0.047298      15        1  2.225354
45    -0.118033  0.005513      16        1  2.213348
37    -0.107990 -0.003646      17        1  2.179590
26     0.137860  0.064464      18        1  2.177700
8      0.102466  0.029958      19        1  2.157230
18    -0.013990 -0.057011      20        1  2.097793
29    -0.076194  0.047684      21        1  2.078674
11     0.070016  0.139853      22        1  2.068465
49    -0.107259  0.045937      23        1  2.066168
41     0.053806  0.067253      24        1  2.002392
9     -0.118009 -0.112129      25        1  1.968771
47    -0.041481  0.125498      26        1  1.954192
35     0.135200 -0.123721      27        1  1.931799
43     0.053482  0.091745      28        1  1.893071
12    -0.001248 -0.024666      29        1  1.869403
21     0.008926 -0.054079      30        1  1.860173
24    -0.044571 -0.010475      31        1  1.839010
30     0.012144  0.117283      32        1  1.815529
5      0.047969  0.044297      33        1  1.796875
28    -0.110905 -0.060402      34        1  1.772580
38     0.042931 -0.074859      35        1  1.767640
1      0.085963  0.077084      36        1  1.765997
17     0.057599 -0.032542      37        1  1.756619
46    -0.001857  0.025514      38        1  1.750793
27     0.035196 -0.067704      39        1  1.737362
14    -0.001571 -0.006275      40        1  1.727174
22    -0.000557  0.075268      41        1  1.692625
32     0.029917  0.040378      42        1  1.679365
2      0.063935  0.129049      43        1  1.668292
20     0.008755 -0.085074      44        1  1.646614
36     0.072030 -0.088120      45        1  1.623347
31    -0.009219 -0.044920      46        1  1.615394
19     0.037397  0.076880      47        1  1.613907
48    -0.043548 -0.006227      48        1  1.601941
42    -0.040269 -0.070384      49        1  1.546049
16     0.028322 -0.080633      50        1  1.360101, topic_info=               Term         Freq        Total Category  logprob  loglift
329        function  1243.000000  1243.000000  Default  30.0000  30.0000
92          android  1299.000000  1299.000000  Default  29.0000  29.0000
117           image  1279.000000  1279.000000  Default  28.0000  28.0000
78          working  1077.000000  1077.000000  Default  27.0000  27.0000
399          window  1096.000000  1096.000000  Default  26.0000  26.0000
...             ...          ...          ...      ...      ...      ...
2735          nuget    24.760430    25.876000  Topic50  -4.7898   4.2535
2487         direct    29.840609    31.190692  Topic50  -4.6032   4.2534
1844  multithreaded    24.302998    25.413998  Topic50  -4.8085   4.2529
209             app    56.944605  1190.726860  Topic50  -3.9570   1.2574
38           python    37.265602  1317.356510  Topic50  -4.3810   0.7323

[1701 rows x 6 columns], token_table=      Topic      Freq      Term
term                           
783      44  0.977810      able
1804     36  0.974436  absolute
456      42  0.962377    accept
839      11  0.012261    access
839      21  0.974742    access
...     ...       ...       ...
21       12  0.975001       yii

### 3.1.2 Modèle 2: LDA entrainement avec titre + body

In [17]:
X_train_merged = X_train_title + X_train_body

In [18]:
X_train_merged.head()

39087    [stored, procedure, function, calling, stored,...
30893    [run, fly, tomcat, netbeans, maven, web, proje...
45278    [show, gray, color, view, io, navigation, bar,...
16398    [form, authentication, ticket, decryption, pos...
13653    [validation, yii, validation, yii, advanced, p...
dtype: object

In [19]:
X_train_title.head()

39087                                  [stored, procedure]
30893                         [run, fly, tomcat, netbeans]
45278    [show, gray, color, view, io, navigation, bar,...
16398    [form, authentication, ticket, decryption, pos...
13653                                    [validation, yii]
Name: Title_tokens, dtype: object

In [20]:
X_train_body.head()

39087    [function, calling, stored, procedure, execute...
30893    [maven, web, project, netbeans, eclipse, refer...
45278    [written, test, ipad, app, contains, split, vi...
16398    [php, developer, almost, nothing, net, asked, ...
13653    [validation, yii, advanced, parent_id, creatin...
Name: Body_tokens, dtype: object

In [21]:
num_topics = 10
perplexity_merged, coherence_score_merged, lda_merged, vis_merged = lda_train(num_topics, X_train_merged)
current_datetime = datetime.now()
formatted_datetime = current_datetime.strftime("%Y-%m-%d %H:%M:%S")
y_resultat = [formatted_datetime, 'lda train avec titre et body', num_topics, perplexity_merged, coherence_score_merged]
performance_list.append(y_resultat)
vis_merged

PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
2     -0.120677  0.052122       1        1  15.624708
0     -0.006181 -0.190631       2        1  12.251810
5      0.058129  0.072682       3        1  11.799788
8      0.154047  0.030490       4        1  10.589980
7     -0.144275  0.031963       5        1   9.438638
6     -0.136476  0.098366       6        1   9.334177
1      0.080635  0.099487       7        1   7.890785
4      0.154061 -0.101635       8        1   7.876885
3     -0.113252 -0.153445       9        1   7.757770
9      0.073988  0.060600      10        1   7.435460, topic_info=           Term          Freq         Total Category  logprob  loglift
129       image   8884.000000   8884.000000  Default  30.0000  30.0000
806        java   7712.000000   7712.000000  Default  29.0000  29.0000
36       server  10958.000000  10958.000000  Default  28.0000  28.0000
244       class   9759.000000   9759.000000  Default  27.0000  27.0000
658      object   8491.000000   8491.000000  Default  26.0000  26.0000
...         ...           ...           ...      ...      ...      ...
1307     apache    546.025779   2064.612920  Topic10  -5.6568   1.2689
648        find    645.345656   5676.199291  Topic10  -5.4897   0.4247
383       could    586.642945   6081.382281  Topic10  -5.5851   0.2603
353   something    573.397976   6071.404980  Topic10  -5.6079   0.2391
100       first    565.127603   6254.476749  Topic10  -5.6224   0.1949

[827 rows x 6 columns], token_table=      Topic      Freq      Term
term                           
3242      3  0.952462  abstract
3242      4  0.004177  abstract
3242      5  0.025065  abstract
3242     10  0.016710  abstract
146       1  0.077662    access
...     ...       ...       ...
2151      9  0.919464   youtube
2151     10  0.003025   youtube
3030      1  0.006178      zone
3030      9  0.006178      zone
3030     10  0.982288      zone

[3432 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[3, 1, 6, 9, 8, 7, 2, 5, 4, 10])

In [22]:
num_topics = 20
perplexity_merged, coherence_score_merged, lda_merged, vis_merged = lda_train(num_topics, X_train_merged)
current_datetime = datetime.now()
formatted_datetime = current_datetime.strftime("%Y-%m-%d %H:%M:%S")
y_resultat = [formatted_datetime, 'lda train avec titre et body', num_topics, perplexity_merged, coherence_score_merged]
performance_list.append(y_resultat)
pyLDAvis.display(vis_merged)

In [23]:
num_topics = 30
perplexity_merged, coherence_score_merged, lda_merged, vis_merged = lda_train(num_topics, X_train_merged)
current_datetime = datetime.now()
formatted_datetime = current_datetime.strftime("%Y-%m-%d %H:%M:%S")
y_resultat = [formatted_datetime, 'lda train avec titre et body', num_topics, perplexity_merged, coherence_score_merged]
performance_list.append(y_resultat)
pyLDAvis.display(vis_merged)

In [24]:
num_topics = 50
perplexity_merged, coherence_score_merged, lda_merged, vis_merged = lda_train(num_topics, X_train_merged)
current_datetime = datetime.now()
formatted_datetime = current_datetime.strftime("%Y-%m-%d %H:%M:%S")
y_resultat = [formatted_datetime, 'lda train avec titre et body', num_topics, perplexity_merged, coherence_score_merged]
performance_list.append(y_resultat)
pyLDAvis.display(vis_merged)

Nous sélectionnons le model avec 20 topics avec titre

### 3.1.3  Modèle 3: LDA entrainement avec titre & tag et body

In [25]:
def lda_train_tag(num_topics, dictionary, X_train):
    # Create a dictionary and bag-of-words representation of the training data
    # dictionary = Dictionary(X_train)
    bow_corpus = [dictionary.doc2bow(doc) for doc in X_train]
    
    # Train the LDA model
    lda_model = LdaModel(corpus=bow_corpus, num_topics=num_topics, id2word=dictionary)

    topics = lda_model.get_document_topics(bow_corpus)
    
    #  Visulisation des topics 
#    vis = pyLDAvis.gensim_models.prepare(topic_model=lda_model, corpus=bow_corpus, dictionary=dictionary, mds='mmds', R=30)
    vis = pyLDAvis.gensim_models.prepare(topic_model=lda_model, corpus=bow_corpus, dictionary=dictionary, mds='pcoa', sort_topics=True)
    
    # Calculer la perplexité
    perplexity = lda_model.log_perplexity(bow_corpus)

    # Calculer la cohérence des topics
    coherence_model = CoherenceModel(model=lda_model, texts=X_train, corpus=bow_corpus, coherence='c_v')
    coherence_score = coherence_model.get_coherence()
    
    return perplexity, coherence_score, lda_model, vis

In [26]:
# Create a set of tokens from X_train_title and X_train_tag
title_tokens_set = set([token for tokens in X_train_title for token in tokens])
tag_tokens_set = set([token for tokens in X_train_tag for token in tokens])

# Get the common tokens that appear in both sets
X_train_union = title_tokens_set.intersection(tag_tokens_set)

train_dictionary_tag = Dictionary([list(X_train_union)])

In [27]:
num_topics = 10
perplexity_tag, coherence_score_tag, lda_tag, vis_tag = lda_train_tag(num_topics, train_dictionary_tag, X_train_merged)
current_datetime = datetime.now()
formatted_datetime = current_datetime.strftime("%Y-%m-%d %H:%M:%S")
y_resultat = [formatted_datetime, 'lda train avec titre&tag + body', num_topics, perplexity_tag, coherence_score_tag]
performance_list.append(y_resultat)
pyLDAvis.display(vis_tag)

In [28]:
num_topics = 20
perplexity_tag, coherence_score_tag, lda_tag, vis_tag = lda_train_tag(num_topics, train_dictionary_tag, X_train_merged)
current_datetime = datetime.now()
formatted_datetime = current_datetime.strftime("%Y-%m-%d %H:%M:%S")
y_resultat = [formatted_datetime, 'lda train avec titre&tag + body', num_topics, perplexity_tag, coherence_score_tag]
performance_list.append(y_resultat)
pyLDAvis.display(vis_tag)

In [29]:
num_topics = 30
perplexity_tag, coherence_score_tag, lda_tag, vis_tag = lda_train_tag(num_topics, train_dictionary_tag, X_train_merged)
current_datetime = datetime.now()
formatted_datetime = current_datetime.strftime("%Y-%m-%d %H:%M:%S")
y_resultat = [formatted_datetime, 'lda train avec titre&tag + body', num_topics, perplexity_tag, coherence_score_tag]
performance_list.append(y_resultat)
pyLDAvis.display(vis_tag)

In [30]:
num_topics = 50
perplexity_tag, coherence_score_tag, lda_tag, vis_tag = lda_train_tag(num_topics, train_dictionary_tag, X_train_merged)
current_datetime = datetime.now()
formatted_datetime = current_datetime.strftime("%Y-%m-%d %H:%M:%S")
y_resultat = [formatted_datetime, 'lda train avec titre&tag + body', num_topics, perplexity_tag, coherence_score_tag]
performance_list.append(y_resultat)
pyLDAvis.display(vis_tag)

In [31]:
train_result = pd.DataFrame(performance_list, columns=['Date', 'Modele', 'nb topics', 'perplexity', 'coherence_score'])
train_result.to_csv('lda_train_result.csv')

### 3.1.4 LDA entrainement avec titre pour fit et titre+body pour transform

In Gensim, the topic modeling models such as LdaModel do not have separate fit and transform methods like in some other machine learning libraries. Instead, the training and transformation steps are combined into a single process.

### 3.1.5 Example des topics découverts 

In [32]:
num_topics = 10

In [33]:
# Create a dictionary and bag-of-words representation of the training data, modèle 1: 
train_dictionary = Dictionary(X_train_title)
train_bow_corpus = [train_dictionary.doc2bow(doc) for doc in X_train_title]

# Train LDA model with 20 topics
lda_model = LdaModel(corpus=train_bow_corpus, num_topics=num_topics, id2word=train_dictionary)

# topics distribution pour chaque docuement dans X_train_title
train_topics_distribution = lda_model.get_document_topics(train_bow_corpus)

In [34]:
# les 10 topics découverts avec les 8 top words
topics = lda_model.print_topics(num_words=8)
for topic in topics:
    words = topic[1].split('+')
    words = [word.split('*')[1].replace('"', '').strip() for word in words]
    print(words)

['object', 'database', 'class', 'property', 'method', 'key', 'mysql', 'attribute']
['type', 'java', 'function', 'node', 'test', 'xml', 'performance', 'exception']
['view', 'change', 'text', 'io', 'best', 'way', 'android', 'swift']
['custom', 'table', 'spring', 'jquery', 'working', 'adding', 'content', 'header']
['php', 'html', 'ajax', 'line', 'form', 'script', 'command', 'jquery']
['array', 'string', 'column', 'python', 'list', 'one', 'row', 'loop']
['image', 'app', 'window', 'android', 'wpf', 'application', 'javascript', 'event']
['api', 'request', 'google', 'http', 'android', 'post', 'model', 'date']
['server', 'web', 'sql', 'button', 'service', 'different', 'application', 'window']
['variable', 'studio', 'visual', 'project', 'azure', 'set', 'used', 'many']


In [35]:
# afficher les probabilité des topics des documents
for i in range(2):
    print(f"Document {i+1} topic distribution:")
    for topic, prob in train_topics_distribution[i]:
        print(f"Topic {topic}: {prob}")
    print()

Document 1 topic distribution:
Topic 0: 0.033334117382764816
Topic 1: 0.033334117382764816
Topic 2: 0.033334117382764816
Topic 3: 0.03333425521850586
Topic 4: 0.033334117382764816
Topic 5: 0.6999927759170532
Topic 6: 0.033334117382764816
Topic 7: 0.033334117382764816
Topic 8: 0.033334117382764816
Topic 9: 0.033334143459796906

Document 2 topic distribution:
Topic 0: 0.22518278658390045
Topic 1: 0.020010432228446007
Topic 2: 0.020007874816656113
Topic 3: 0.020009726285934448
Topic 4: 0.020008238032460213
Topic 5: 0.020008906722068787
Topic 6: 0.37547746300697327
Topic 7: 0.2592694163322449
Topic 8: 0.02001725509762764
Topic 9: 0.020007874816656113



## 3.2 prédiction de topics et les mots

In [36]:
def predit_word(num_topics, X_train, X_test):
    # Prédict la topics distribution for each document in the test set X_test_title
    train_dictionary = Dictionary(X_train)
    train_bow_corpus = [train_dictionary.doc2bow(doc) for doc in X_train]
    
    # Train the LDA model
    lda_model = LdaModel(corpus=train_bow_corpus, num_topics=num_topics, id2word=train_dictionary)
    
    # création bow pour X_test_title avec les dictionary train  (avec test_body et option)    
    test_bow_corpus = [train_dictionary.doc2bow(doc) for doc in X_test]
    test_topics_distributions = lda_model[test_bow_corpus] 
    
    # Extract keywords from the inferred topic distributions
    test_keywords = []
    for doc_topics in test_topics_distributions:       
    # trier les topics par la probailité en order décroissant (x[1] de doc_topics)
        sorted_topics = sorted(doc_topics, key=lambda x: x[1], reverse=True)
    # extraire le premier mot clé des top topics 
        top_keywords = [train_dictionary[word_id] for word_id, _ in sorted_topics[:10]]  # Adjust the number of keywords as needed
        test_keywords.append(top_keywords)
    return test_keywords

In [37]:
def predit_word_full(num_topics, X_train, X_test):
    # Prédict la topics distribution for each document in the test set X_test_title
    train_dictionary = Dictionary(X_train)
    train_bow_corpus = [train_dictionary.doc2bow(doc) for doc in X_train]
    
    # Train the LDA model
    lda_model = LdaModel(corpus=train_bow_corpus, num_topics=num_topics, id2word=train_dictionary)
    
    # création bow pour X_test_title avec les dictionary train  (avec test_body et option)    
    test_bow_corpus = [train_dictionary.doc2bow(doc) for doc in X_test]
    test_topics_distributions = lda_model[test_bow_corpus] 

    #print("test_bow_corpus = ", test_bow_corpus)
    #print("test_topics_distributions = ", test_topics_distributions)
    
    # Extract keywords from the inferred topic distributions
    test_keywords = []
    for doc_topics in test_topics_distributions:       
    # trier les topics par la probailité en order décroissant (x[1] de doc_topics)
        sorted_topics = sorted(doc_topics, key=lambda x: x[1], reverse=True)
    # extraire le premier mot clé des top topics 
        top_keywords = [train_dictionary[word_id] for word_id, _ in sorted_topics[:10]]  # Adjust the number of keywords as needed
        test_keywords.append(top_keywords)
    return test_keywords, train_dictionary, lda_model

### 3.2.1 Prediction avec modèle 1 

In [38]:
num_topics = 20

In [39]:
test_keywords_m1 = predit_word(num_topics, X_train_title, X_test_title)

In [40]:
print(test_keywords_m1[:5])

[['uisplitviewcontroller', 'php', 'form', 'procedure', 'stored', 'fly', 'netbeans', 'run', 'tomcat', 'bar'], ['show', 'form', 'navigation', 'view', 'bar'], ['view', 'uisplitviewcontroller', 'tomcat', 'navigation'], ['possible', 'color', 'fly', 'procedure', 'stored', 'netbeans', 'run', 'tomcat', 'bar', 'gray'], ['view', 'authentication', 'color', 'form']]


In [41]:
test_keywords_m1, train_dictionary, lda_model = predit_word_full(num_topics, X_train_title, X_test_title)

In [42]:
print(test_keywords_m1[:5])

[['stored', 'decryption', 'php', 'procedure', 'fly', 'netbeans', 'run', 'tomcat', 'bar', 'color'], ['navigation', 'php', 'ticket', 'uisplitviewcontroller', 'run'], ['php', 'form', 'ticket'], ['uisplitviewcontroller', 'color', 'fly', 'procedure', 'stored', 'netbeans', 'run', 'tomcat', 'bar', 'gray'], ['uisplitviewcontroller', 'bar', 'color']]


In [43]:
import pickle

with open('lda_model.pkl', 'wb') as model_file:
    pickle.dump(lda_model, model_file)
with open('train_dictionary.pkl', 'wb') as dictionary_file:
    pickle.dump(train_dictionary, dictionary_file)    

### 3.2.2 Prediction avec modèle 2 

In [44]:
num_topics = 30

In [45]:
test_keywords_m2 = predit_word(num_topics, X_train_title + X_train_body,  X_test_title + X_test_body)

In [46]:
print(test_keywords_m2[:5])

[['net', 'copy', 'directly', 'fly', 'sql', 'function', 'passing', 'chose'], ['execute', 'getting', 'calling', 'return', 'directly'], ['net', 'calling', 'eclipse', 'maven', 'clean', 'stored', 'advance'], ['maven', 'call', 'bam', 'eclipse', 'procedure', 'clean'], ['getting', 'sql', 'chose', 'go']]


### 3.2.2 Prediction avec modèle 3

In [47]:
def predit_word_tag(num_topics, train_dictionary, X_train, X_test):
    # Prédict la topics distribution for each document in the test set X_test_title
    # train_dictionary = Dictionary(X_train)
    train_bow_corpus = [train_dictionary.doc2bow(doc) for doc in X_train]
    
    # Train the LDA model
    lda_model = LdaModel(corpus=train_bow_corpus, num_topics=num_topics, id2word=train_dictionary)
    
    # création bow pour X_test_title avec les dictionary train  (avec test_body et option)    
    test_bow_corpus = [train_dictionary.doc2bow(doc) for doc in X_test]
    test_topics_distributions = lda_model[test_bow_corpus] 
    
    # Extract keywords from the inferred topic distributions
    test_keywords = []
    for doc_topics in test_topics_distributions:       
    # trier les topics par la probailité en order décroissant (x[1] de doc_topics)
        sorted_topics = sorted(doc_topics, key=lambda x: x[1], reverse=True)
    # extraire le premier mot clé des top topics 
        top_keywords = [train_dictionary[word_id] for word_id, _ in sorted_topics[:10]]  # Adjust the number of keywords as needed
        test_keywords.append(top_keywords)
    return test_keywords

In [48]:
# Create a set of tokens from X_train_title and X_train_tag
title_tokens_set = set([token for tokens in X_train_title for token in tokens])
tag_tokens_set = set([token for tokens in X_train_tag for token in tokens])

# Get the common tokens that appear in both sets
X_train_union = title_tokens_set.intersection(tag_tokens_set)

train_dictionary_tag = Dictionary([list(X_train_union)])

In [49]:
num_topics = 10

In [50]:
test_keywords_m3 = predit_word_tag(num_topics, train_dictionary_tag, X_train_title, X_test_title)

In [51]:
print(test_keywords_m3[:5])

[['abstract', 'aar', 'acceptance', 'abstraction', 'acceleration', 'accelerometer', 'abide', 'abi', 'abort', 'absolute'], ['abstraction', 'abstract', 'accelerometer', 'abort', 'acceleration', 'abi', 'absolute', 'abide', 'acceptance', 'aar'], ['absolute', 'accelerometer', 'abstraction', 'abstract', 'aar', 'abort', 'abi', 'acceptance', 'acceleration', 'abide'], ['abi', 'abide', 'abstraction', 'absolute', 'accelerometer', 'abort', 'aar', 'abstract', 'acceptance', 'acceleration'], ['aar', 'accelerometer', 'acceleration', 'abstraction', 'abstract', 'absolute', 'abi', 'abide', 'abort', 'acceptance']]


## 3.3 Mesure de prediction

In [52]:
def prediction_couverture(predits, reels): 

    # Convertir les colonnes des dataframes en listes de tokens
    mots_cles_reels = reels.tolist()  # convert token to list de strings
    mots_cles_predits = predits

    # Compteur de mots clés réels correctement prédits
    mots_cles_corrects = 0

    # Parcourir les mots clés réels
    for mots_reels in mots_cles_reels:  # pour chaque document
        for mot_reel in mots_reels:     # chaque mot reel du document
        # si un mot réel est parmi les mots prédits
            if any(mot_reel in mots_predits for mots_predits in mots_cles_predits):
                mots_cles_corrects += 1
                break

    # Calculer le taux de couverture des tags réels
    taux_couverture = mots_cles_corrects / len(mots_cles_reels) * 100

    # Afficher le taux de couverture des tags réels
    print("Taux de couverture des tags réels :", taux_couverture, "%")
    return taux_couverture

In [53]:
couverture_m1 = prediction_couverture(test_keywords_m1,X_test['Tag_token'])

Taux de couverture des tags réels : 10.93 %


In [54]:
couverture_m2 = prediction_couverture(test_keywords_m2,X_test['Tag_token'])

Taux de couverture des tags réels : 18.89 %


In [55]:
couverture_m3 = prediction_couverture(test_keywords_m3,X_test['Tag_token'])

Taux de couverture des tags réels : 0.2 %
